# Chapter 4: Statistical Data Analysis II - Parameter Estimation (Part 4)

## Numerical optimization (optional)
Algorithms for numerical optimization are currently used in many areas of society and science:
- In physics, **models are fitted to measurement data** derived from physics theories. This allows the parameters of the model or theory to be determined experimentally.
- In business, **technical systems are numerically optimized**, e.g., the optimal assignment of aircraft to gates at the airport is an interesting optimization problem.
- Most current methods of artificial intelligence (AI) are based on **deep machine learning**. AI models ultimately represent complicated non-linear functions of the input values whose parameters are "trained" - this is also a numerical optimization problem. Current AI models, e.g., large language models, can contain up to [$10^{12}$ parameters](https://epochai.org/data/epochdb/visualization?yAxis=Parameters).

The numerical optimization process requires the following "ingredients", which must be made available to the algorithm:
- The **function to be minimized** is often referred to as the loss function, cost function, or objective function. It is often a complicated function that depends on (potentially many) parameters with respect to which it is to be minimized.
- Parameters of the optimization algorithm, often called **meta-parameters**, such as step sizes of algorithms or convergence criteria.
- It may also be possible to formulate **constraints**, e.g., value ranges for parameters.

Determining the **global minimum** of a complicated function is often a challenge for optimization algorithms. The algorithms used for this purpose often have mechanisms to prevent the minimization from getting "stuck" in a local minimum.

### Methods for function minimization
Function minimization methods can be roughly divided into three classes. The first two methods are based on the search for minima by evaluating the function at grid points:
- In **grid search**, the loss function is evaluated on a fixed grid of grid points and the minimum function value is searched for. Since the function is not known a priori, grid points with the same distance are often used. This class of methods does not scale well with high-dimensional functions: with $k$ grid points per dimension, $k^d$ function evaluations are required for $d$ dimensions. One way to improve the method is to use a customized grid with tighter spacing where the function values change significantly.
- A **Monte Carlo search** evaluates the loss function at randomly distributed grid points. This method is related to Monte Carlo integration. Like all Monte Carlo methods, this is more efficient than a grid search, especially for high-dimensional functions. The "art" is to distribute the support points smartly. As with the grid search, more random support points should be generated where the function values change significantly.

The third class includes **numerical optimization methods** and can be further subdivided into
- **direct search methods**, which use a well-motivated but simple and robust rule for function evaluation to advance step by step to the minimum, and
- **iterative methods**, which are based on the first and/or second derivative of the function and find the way to the minimum with the help of these derivations.
    
In SciPy, a number of common methods for function minimization are implemented in `scipy.optimize.minize()`.

### Rosenbrock function
An example function that is  frequently used for testing optimization methods is the **Rosenbrock function**, sometimes also referred to as the "banana function":
$$
f(x,y) = (a-x)^2 + b( y-x^2)^2.
$$
For the parameter choice $a=1$ and $b=100$, this function has a global minimum at $(x,y)=(1,1)$. Around this minimum, however, there is a flat valley along the banana shape, which poses a challenge for optimization methods. The Rosenbrock function and its minimum are plotted with this parameter choice in the following code example with `scipy.optimize.rosen`:

In [ ]:
"""Rosenbrock function: standard example of numerical optimization"""

import numpy as np
import matplotlib
import matplotlib.pyplot as plt

x = np.linspace( -1.5, 1.5, 300 )
y = np.linspace( -1, 2, 300 )
X, Y = np.meshgrid( x, y )

rosen = lambda x, y: ( 1 - x )**2 + 100*( y - x**2 )**2
Z = rosen( X, Y )
levels = np.logspace( -2, 3, 16 )

fig, ax = plt.subplots()
CS = ax.contourf( X, Y, Z, levels, cmap=matplotlib.cm.gray, norm=matplotlib.colors.LogNorm() )
fig.colorbar( CS, ax=ax )
ax.plot( 1, 1, marker="o", color="orange" )
ax.set_xlabel( r'$x$' )
ax.set_ylabel( r'$y$' )

plt.show()

### Simplex method
The **simplex method** (John Nelder, Roger Mead, 1965) is a **heuristic method** for the direct search for function minima. **Heuristics** are practical methods that find "good" solutions for a task (here the minimum search) with limited information. The heuristic of the simplex method is based on a geometric object called a **simplex**. In two dimensions, the simplex is a triangle. However, this concept can also be extended to $d$ dimensions. Then the simplex is a $d$-dimensional polyhedron consisting of $d+1$ points. Nelder and Mead's algorithm is based on the idea of systematically changing the simplex so that it converges to the minimum of a function. To do this, in each step the point on the simplex that has the "worst" function value is replaced by a better point. To do this, the simplex can be mirrored at the other points, it can be expanded or contracted in one direction or shrunk overall. The method is very robust because it only requires function values, no derivatives. On the other hand, it is often inefficient, i.e., it takes a relatively long time to converge to the minimum. There is also a risk of convergence to a local minimum. The following animation illustrates the procedure (source: Nicoguaro, [Nelder-Mead_Rosenbrock.gif](https://commons.wikimedia.org/w/index.php?title=File:Nelder-Mead_Rosenbrock.gif&oldid=260874010), CC BY 4.0, where you can also find the corresponding Python code):

<img src="img/Nelder-Mead_Rosenbrock.gif" width=50%>


>**Nelder-Mead algorithm in detail**
>
>The Nelder-Mead algorithm is intended to minimize the function $f(\mathbf{x})$. The simplex consists of $n+1$ points $\mathbf{x}_i$ in $\mathbb{R}^n$. The algorithm consists of the following steps:
>
>Step 1: **Sort** $\mathbf{x}_i$ by increasing function values $f(\mathbf{x}_i)$, test **termination condition** (e.g., fixed number of steps, size of the simplex)
>
>Step 2: Calculate **center of gravity** of $\mathbf{x}_1, \dots, \mathbf{x}_n$:
>$$
\mathbf{x}_S = \frac{1}{n}\sum_{i=1}^n \mathbf{x}_i.
>$$
>
>Step 3: **Mirror** $\mathbf{x}_{n+1}$ with $\mathbf{x}_S$:
>$$
\mathbf{x}_r = \mathbf{x}_S + \alpha( \mathbf{x}_S - \mathbf{x}_{n+1} ).
>$$
>with $\alpha > 0$ reflection parameter (e.g., $\alpha=1$) $\to$ if $f(\mathbf{x}_1) < f(\mathbf{x}_r) < f(\mathbf{x}_n)$: replace $\mathbf{x}_{n+1}$ with $\mathbf{x}_r$ and go to step 1.
>
>Step 4: If $f(\mathbf{x}_r) < f(\mathbf{x}_1)$: **expand** simplex,
>$$
\mathbf{x}_e = \mathbf{x}_S + \gamma( \mathbf{x}_r - \mathbf{x}_S ),
>$$
> with $\gamma > 0$ expansion parameter (e.g. $\gamma = 2$) $\to$ if $f(\mathbf{x}_e) < f(\mathbf{x}_r)$ replace $\mathbf{x}_{n+1}$ by $\mathbf{x}_e$, otherwise by $\mathbf{x}_r$, and go to step 1.
>
>Step 5: Now $f(\mathbf{x}_r) > f(\mathbf{x}_n)$ applies: **contract** simplex,
>$$
\mathbf{x}_c = \mathbf{x}_S + \rho( \mathbf{x}_{n+1} - \mathbf{x}_S ),
>$$
> with $\rho > 0$ contraction parameter (e.g., $\rho = 0.5$) $\to$ if $f(\mathbf{x}_c) < f(\mathbf{x}_{n+1})$: replace $\mathbf{x}_{n+1}$ with $\mathbf{x}_c$ and go to step 1.
>
>Step 6: **Shrink** simplex by substitution
>$$
\mathbf{x}_i = \mathbf{x}_1 + \sigma( \mathbf{x}_{i} - \mathbf{x}_1 )
>$$
>for all $i > 1$ with $\sigma > 0$ shrinkage parameter (e.g., $\sigma=0.5$) and go to step 1.

### Gradient method
The **gradient descent** (also: steepest descent) is an example of the class of **iterative methods**. The basic idea of all these methods is to find the direction of descent $\mathbf{d}_i$ of the loss function $f(\mathsf{x})$ at the point $\mathbf{x}_i$. The next point $\mathbf{x}_{i+1}$ is then reached by a step in this direction: $\mathbf{x}_{i+1} = \mathbf{x}_i + t_i \mathbf{d}_i$. The parameter $t_i$ specifies the **step size**, in the field of machine learning it is also often referred to as **learning rate**. This descent along the descent direction is carried out until a termination criterion is met.

The gradient method uses the **direction of the steepest descent** for the descent direction.Tathematically this is the negative gradient:
$$
\mathbf{d}_i = -\nabla f(\mathbf{x_i}).
$$
The method requires the first derivative of the function and is therefore referred to as a first-order algorithm. It is illustrated in the following figure using the Rosenbrock function. The arrows are the individual steps, each in the direction of the largest negative gradient at the starting point:

<img src="img/gradient_descent.png" width=40%>

The "art" of the gradient method is to select the step size so that $f(\mathbf{x}_i)$ decreases as quickly as possible and the minimum is reached in as few steps as possible. A step size that is too small leads to a too large number of steps and therefore to slow convergence. It also carries the risk of getting "stuck" in local minima. If the step size is too large, the algorithm could "overshoot the minimum", which in turn leads to slow convergence. Modern optimization algorithms such as [Adam](https://arxiv.org/abs/1412.6980) therefore also use stochastic elements (evaluation only on part of the data) and/or are based on physical concepts such as momentum.

## Outlook: Modern methods of data analysis
This course on computer-aided data analysis only provides initial insight into the analysis of data using a computer. Many other, more in-depth methods and algorithms are used in science and business. These include, among others:
- The **maximum likelihood method** as the basis of many modern methods of data analysis.
- More complex methods of **model fitting**, e.g. with constraints and/or constraints.
- **Interval estimation** in the context of frequentist statistics (confidence intervals) or Bayesian statistics (credible intervals).
- **Hypothesis testing** and statistical classification.
- **Machine learning** as a current core area of artificial intelligence (AI).

When studying physics at KIT, you will come into contact with such methods in many fields of research, especially in particle and astroparticle physics. In the 5th semester of the Bachelor's study program in Physics, an **elective course on data analysis** is offered, which lays further foundations for a Bachelor's thesis in data analysis. The course "Modern Methods of Data Analysis", which covers advanced topics from the field of "data science", is part of the curriculum of the Master's study program in Physics at KIT.

### Maximum Likelihood Method
#### Overview
The **maximum likelihood (ML) method** was introduced by Ronald Aylmer Fisher around 1912. As in the method of least squares (LS method), parameter estimation in the ML method is based on the search for extreme values of a function so that a statistical model best "fits" the data. This function is called the **likelihood function** and its maximization leads to estimators for parameters. In contrast to the LS method, which only works well under certain conditions, the ML method is universally applicable and forms the basis of many advanced statistical methods such as hypothesis testing. The ML method has a number of "good properties": among other things, it is **efficient**, i.e., it provides the smallest possible variance of the estimator and therefore the lowest possible uncertainty. For random variables that follow a normal distribution, the **LS method and ML method are equivalent**, i.e., they provide the same estimator for variables such as the expected value and variance of a distribution.

>**Excursus: Properties of estimators**
>
>In the following, we will briefly describe in words which properties of estimators are considered to be particularly favorable. There is a mathematical formulation for (almost) all of these properties, which is discussed in advanced courses and in the statistical literature. An estimator should be:
>- **Bias-free**: an estimator with small or no bias is desirable. Bias is the deviation of the expected value from the true value. The arithmetic mean, which is the estimator for the expected value in both the LS and ML methods, is true to expectation. In contrast, the estimators of the LS and ML method for the variance is an example of a biased estimator. Only the Bessel correction produces an estimator that is true to expectation, the sample variance.
>- **Consistent**: an estimator is called consistent if it converges to the true value in the limiting case of large samples. The sample variance without Bessel correction is biased for small samples, but converges to the true value for large samples. It is therefore not true to expectation, but consistent.
>- **Efficient**: an estimator is described as efficient if it has the smallest possible variance. Efficient estimator can therefore determine parameters with the lowest possible uncertainty. This is discussed in the statistical literature under the keyword [Cramér-Rao bound](https://en.wikipedia.org/wiki/Cramér–Rao_bound). Efficient estimators are one of the great advantages of the ML method.
>- **Accuracate**: the accuracy of an estimator is measured by its mean squared error (MSE), the sum of the variance and the square of the bias. High accuracy is therefore a combination of low variance and low bias.
>- **Robust**: a robust estimator is less sensitive to "outliers" in data or a faulty model. For example, the arithmetic mean as an LS and ML estimator for the expected value is susceptible to outliers, whereas the median is much more robust.
>- **Simple**: often a simple definition of an estimator, and thus often a simple implementation in computer code, must be weighed against other criteria such as fidelity to expectations.

The different approaches of the LS method and the ML method for solving the question "Which model parameters best fit the data?" are now to be compared:
- The **LS method** minimizes the residual sum of squares, i.e., the distance of the data points $y_i$ from the expected value of the model function $\lambda_i$, normalized to the variance $\sigma_i^2$:
    $$
    S \equiv\chi^2\equiv \sum_i \frac{(y_i-\lambda_i)^2}{\sigma_i^2} \overset{!}{=}\mathsf{min}
    $$
    and only these two variables need to be known.
- The **ML method** maximizes the functional value of the probability density function (PDF) at the location of the measurement, as will be introduced in more detail below. To do this, the entire PDF must be known, not just the expected value and variance.

This difference in approach is illustrated in the following code example. A normal distribution is used as the model function; it is shown for three different parameter sets. The measurement (red arrow) is compared using the LS and ML methods. Both methods are equivalent for normal distributions, but they follow a different approach. The LS method determines the **quadratic distance from the expected value** (dashed line) and normalizes it to the variance (not shown). The ML method evaluates the **functional value of the PDF** (dotted line) at the measured value.

In [ ]:
"""Illustrate difference of least squares methode and maximum likelihood method"""
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import norm

x = np.linspace( -5, 5, 200 )
xm = 1.75
mu  = [0,0,1]
sig = [1,2,1]   

fig, ax = plt.subplots( 1, 3, figsize=(15,4) )

# plot PDFs with different model parameters
for l, s, a in zip( mu, sig, ax ):
    # plot curve
    line, = a.plot( x, norm.pdf( x, loc=l, scale=s ), label=r"$\mu=%d, \sigma=%d$" % ( l, s )  )

    # annotate
    pdfl = norm.pdf( l, loc=l, scale=s )    
    pdfm = norm.pdf( xm, loc=l, scale=s )
    a.vlines( l, 0, pdfl, linestyles="dashed", colors=line.get_color() )
    a.hlines( pdfm, -3.5, 3.5, linestyles="dotted", colors=line.get_color() )
    a.arrow( xm, 1.2*pdfm, 0, -1.2*pdfm, head_width=0.15, head_length=0.02, length_includes_head=True, color="r" )
    a.text( xm - 0.1, 1.2*pdfm+0.01, "Measurement", color="r" )
    a.annotate( "", xy=(l, 0.05), xytext=(xm,0.05), arrowprops=dict(arrowstyle="<->",linestyle="dashed",color=line.get_color()) )
    a.annotate( "", xy=(-3, 0), xytext=(-3,pdfm), arrowprops=dict(arrowstyle="<->",linestyle="dotted",color=line.get_color()) )
               
    a.set_xlabel( "$x$")
    a.set_ylabel( "Probability Density Function" )
    a.set_ylim( 0, 0.45 )
    a.legend()

plt.show()

>**Note:** With the ordinary LS method, i.e., without normalization to the variance, the first two cases would be indistinguishable.

#### Likelihood function

The central variable used within the maximum likelihood method for parameter estimation is the **likelihood function** $L$. In order to construct it, the PDF $f(x;\mathbf{a})$ must be known for measured values $\mathbf{x}\equiv(x_1,\dots,x_n)^\mathsf{T}$ from a sample of size $n$. Here, $f$ is a PDF in the probability space of the random variable $x$ (see Chapter 2) and is normalized to one in this space,
$$
\int f(x;\mathbf{a})\,\mathsf{d}x = 1.
$$

The PDF depends on $m$ parameters $\mathbf{a}\equiv(a_1,\dots,a_m)^\mathsf{T}$. The **likelihood function** is defined as the **product of the probability density functions** of all measurements:
$$
L(\mathbf{a}) \equiv L(\mathbf{a}|\mathbf{x})
\equiv \prod\limits_{i=1}^n f(x_i;\mathbf{a}).
$$
This function assumes larger values the better the parameters $\mathbf{a}$ "fit" the data. The notation $L(\mathbf{a})$ or $L(\mathbf{a}|\mathbf{x})$ is intended to indicate that the likelihood function is a **function of the parameters**, i.e., it "lives" in the parameter space. $L$ is therefore evaluated *after* the measurement, i.e., the $x_i$ **are fixed** and have already been inserted into $L$. We also interpreted the residual sum of squares $S\equiv\chi^2$ for the LS methods as a function of $\mathbf{a}$ in the same way. Note that $L$ **is not a PDF in parameter space** and is therefore not normalized to one.

#### Maximum Likelihood Principle
The principle of the maximum likelihood method for parameter estimation can now be formulated using the likelihood function:

>**Maximum Likelihood Principle** 
>
>The maximum likelihood estimate $\hat{\mathbf{a}}$ for a parameter vector $\mathbf{a}$ is the value of $\mathbf{a}$ for which the likelihood function assumes the largest value:
>$$
L(\hat{\mathbf{a}}) \geq L(\mathbf{a}) \quad\forall \mathbf{a}.
>$$

The maximum likelihood principle therefore involves the **maximization** of the likelihood function $L$. In practice, however, the **negative logarithm** of $L$ (negative log likelihood, NLL) is almost always **minimized**:
$$
-\ln L(\mathbf{a}) \overset{!}{=}\mathsf{min}
$$
Since the logarithm is a strictly monotonic function, $-\ln L(\mathbf{a})$ has a minimum exactly where $L(\mathbf{a})$ has a maximum. The necessary condition for the estimated value $\hat{\mathbf{a}}$ is therefore
$$
\frac{\partial (-\ln L(\mathbf{a}))}{\partial a_j} \overset{!}{=} 0.
$$
The sufficient condition for a minimum at $\hat{\mathbf{a}}$ is that the matrix of the second partial derivatives (Hessian matrix) is
$$
\left.\frac{\partial^2 (-\ln L(\mathbf{a}))}{\partial a_i\,\partial a_j}\right|_{\mathbf{a} = \mathbf{\hat a}}
$$
is negative definite, i.e., the likelihood function is a convex function. The minimization of $-\ln L(\mathbf{a})$ is analytically possible in a few cases, but in most cases it is carried out numerically.

Using $-\ln L(\mathbf{a})$ has the following advantages:
- By forming the logarithm, products become sums:
    $$
    -\ln L(\mathbf{a}) = -\sum_{i=1}^n f(x_i;\mathbf{a}).
    $$
- When logarithmizing, constant factors become constant summands. These constant summands play no role for the minimum of a sum: they shift all function values up or down and are omitted when forming the derivative and can therefore be omitted in the numerical minimization. This often saves computing time, e.g., when factorials occur as in the Poisson PDF (Chapter 2).
- For a numerical evaluation of the likelihood function, it is helpful that the logarithm of $L$ is numerically much smaller than $L$ itself. It is not unusual for $L$ to become numerically very large and thus the numerical accuracy of the floating point representation in the computer reaches its limits. For a 32-bit floating point number, the largest value that can be displayed is $3.4028235\times 10^{38}$. The natural logarithm of this number is 88.7228, this value can be represented much better with floating point numbers.

In the following code example, the data points and the negative log-likelihood function calculated from them for $n=1$ to $n=5$ normally distributed random numbers with localization parameter $\mu=5$ and scaling parameter $\sigma=1$ are displayed graphically. Analogous to the LS method, this results in a parabola around the estimated value $\hat{\mu}$, which is increasingly curved with adding more random numbers.

In [ ]:
"""Maximum likelihood method: negative log likelihood for more and more data"""

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as anim

# construct negative log likelihood function for Gaussian
def NLL_gaussian( mu, sigma, data ):

    sig2 = sigma**2

    # constant terms ignored as they are irrelevant for the function's minimum
    #N = len( data )
    #const = 0.5 * N * ( np.log(2*np.pi) + np.log( sig2 ) )

    # construct negative log likelihood the Python/NumPy way
    DATA, MU = np.meshgrid( data, mu )
    return np.sum( 0.5*(DATA-MU)**2/sig2, axis=1 )

    # this is equivalent to, but less readable than, the following
    #NLL = 0
    #for i in np.arange( N ):
    #    NLL += 0.5*(data[i]-mu)**2/sig2
    # return NLL

# true model parameters
atrue = 5
sig   = 1

# data points
n = 5
steps = 500
xi = np.linspace( 1, n, n )
xrange = np.linspace( 0.5, n + 0.5, steps )

# scan of a values
mumin, mumax = 0., 10.
mu = np.linspace( mumin, mumax, steps )

rng = np.random.default_rng( 42 )
yi = rng.normal( loc=atrue, scale=sig, size=n )

fig,ax = plt.subplots( 2, 5, figsize=(25,10) )

for i in np.arange( len(yi) ):
    # compute NLL for first i data points
    NLL = NLL_gaussian( mu, sig, yi[:i+1] )

    NLL_min = np.amin( NLL )
    muhat = np.mean( yi[:i+1] ) # using our knowledge that the ML estimator is the mean

    # plot data points
    ax[0][i].errorbar( xi[:i+1], yi[:i+1], yerr=sig, fmt="ro" )
    ax[0][i].set_xlabel( r"$x$")
    ax[0][i].set_ylabel( r"$y$")
    ax[0][i].set_xlim( 0, 6 )
    ax[0][i].set_ylim( 0, 8 )
    ymean = np.repeat( muhat, steps )
    ax[0][i].plot( xrange, ymean, "r--" )

    # plot NLL
    ax[1][i].set_title( r"%d random number(s): $\hat{\mu} = %4.3f$" % ( i+1, muhat ) )
    ax[1][i].plot( mu, NLL-NLL_min )
    ax[1][i].set_xlabel( r"$\mu$")
    ax[1][i].set_ylabel( r"$\Delta(-\ln L(\mu))$")
    ax[1][i].set_xlim( 0, 10 )
    ax[1][i].set_ylim( 0, 50 )

plt.show()

#### Maximum likelihood: analytical solution
For a normal distribution, the likelihood function can be minimized **analytically**. This demonstrates the equivalence of the ML method and the LS method at the same time. We write the likelihood function explicitly as
$$
L(\mu,\sigma) = \prod\limits_{i=1}^{n} \frac{1}{\sqrt{2\pi}\,\sigma}
\exp\left[
-\frac{(x_i - \mu)^2}{2\sigma^2}
\right].
$$
Reminder: $L$ is a function of the parameters $\mu$ and $\sigma$, not of the data. The negative natural logarithm of this expression is then given by
$$
-\ln L(\mu,\sigma) = \frac{1}{2} \sum\limits_{i=1}^{n}
\left[
\ln(2\pi) + \ln(\sigma^2) + \frac{(x_i - \mu)^2}{\sigma^2}
\right],
$$
where the calculation rule for the logarithm $\ln x^a$ = $a\ln x$ was used. The constant summands $1/2 \cdot n \cdot (\ln(2\pi) + \ln(\sigma^2) )$ are irrelevant for the minimum and can be omitted. The remaining summands describe a parabola in the parameter $\mu$. The comparison with the residual sum of squares,
$$
S \equiv \sum_{i=1}^{n} \frac{(x_i - \mu)^2}{\sigma_i^2},
$$
shows that in the case that the $x_i$ all come from the same PDF and therefore have the same variance $\sigma_i^2\equiv\sigma^2$, both variables are equal except for a factor of 1/2 and the constant summands mentioned above:
$$
-\ln L = \frac{1}{2} S + \mathsf{const}.
$$
Both have the same minimum for a normal distribution, which we already calculated analytically at the beginning of chapter 4, and therefore both provide **the same estimated value**. For other distributions, the **ML method and the LS method are generally not equivalent**.

The minimization of the NLL can also be carried out analytically for the **Poisson distribution**. The NLL results from the Poisson PDF as
$$
\begin{split}
L(\nu) &= \prod\limits_{i=1}^N \frac{\nu^{n_i}}{n_i!}\exp[-\nu]\\
-\ln L(\nu) &= \sum\limits_{i=1}^N
\left[
-n_i \ln\nu + \ln(n_i!) + \nu
\right] \\
&=N\nu - \sum\limits_{i=1}^N n_i \ln\nu + \textsf{const}.
\end{split}
$$
The minimum of the NLL is obtained from the following short calculation
$$
\begin{split}
\frac{\partial \ln (-L(\nu))}{\partial \nu} &=
N - \sum\limits_{i=1}^N\frac{n_i}{\nu} \overset{!}{=} 0\\
\quad\to\quad
\hat\nu &= \frac{1}{N}\sum\limits_{i=1}^N n_i.
\end{split}
$$
This again results in the arithmetic mean of the measured values as the ML estimate for the expected value. The constant term is omitted in the minimization. This is numerically advantageous because this term contains factorials of possibly large numbers.

#### Variance of maximum likelihood estimates
The **graphical method** already known from the least squares method for determining the variance also works in a very similar way for the maximum method, even for non-normally distributed random numbers. The idea is again to expand the negative log-likelihood function around its minimum up to the quadratic term:
$$
-\ln L(a) \approx
-\ln L(\hat{a})
+ \left.\frac{\partial(-\ln L(a))}{\partial{a}}\right|_{a = \hat{a}}
(a - \hat{a})
+ \frac{1}{2} \left.\frac{\partial^2(-\ln L(a))}{\partial a^2}\right|_{a = \hat{a}}
(a - \hat{a})^2.
$$
The first derivative vanishes again at the minimum and a relationship with the inverse of the variance $\mathsf{V}[\hat{a}]^{-1}$ can be established again for the second derivative. However, this is no longer so easy to obtain from the linear law of uncertainty propagation, but must be shown using the Cramér-Rao bound mentioned above - this is discussed in advanced textbooks and lectures on statistical data analysis. As an approximation, the interval $\hat{a}\pm\sqrt{\mathsf{V}[\hat{a}]}\equiv\hat{a}\pm\sigma_{\hat{a}}$ is given by
$$
\begin{split}
-\ln L(a) &\approx -\ln L(\hat{a}) + \frac{1}{2} \\
\quad\to\quad
\Delta(-\ln L(a)) &\equiv -\ln L(a) - (- \ln L(\hat a)) \approx \frac{1}{2}.
\end{split}
$$
The uncertainty of the parameter estimate can therefore be obtained by a scan of the negative log-likelihood function for the function value $-\ln L(\hat{a}) + 1/2$, a horizontal line at a vertical distance of 1/2 from the minimum. Sometimes $-2\ln L(\hat{a})$ is also plotted, in which case the distance of the horizontal line from the minimum is one. The following code example illustrates this for a Poisson distribution. For this distribution, the negative log-likelihood function is not a parabola.

In [ ]:
""" Variance of ML estimators (example: Poisson)"""

import numpy as np
import matplotlib.pyplot as plt

def NLL_poisson( nu, data ):
    """construct negative log likelihood function for Poisson distribution"""
    
    N = len( data )
    ln_nu = np.log( nu )

    # constant terms ignored as they are irrelevant for the function's minimum

    # const = sum ln n! 

    # construct negative log likelihood the Python/NumPy way
    DATA, LN_NU = np.meshgrid( data, ln_nu )
    return N * nu - np.sum( DATA * LN_NU, axis=1 )

    # this is equivalent to, but less readable than, the following
    # NLL = N * nu
    #for i in np.arange( N ):
    #    NLL -= data[i] * ln_nu 
    #return NLL

# function for equivalent parabola (using second derivative at minimum)
def NLL_parabola( x, xmin, ymin, ddymin ):
    return ymin + 0.5*ddymin*(x-xmin)**2

# Data: 5 Poisson distributed data points
npoints = 5
nu = 5

x,dx = np.linspace( 1, 11, 1000, retstep=True )
rng = np.random.default_rng()
data = rng.poisson( nu, npoints )

# NLL for first datapoint
fig,ax = plt.subplots()
xmin = np.mean( data )
imin = np.searchsorted( x, xmin, side='left' )

# NLL minus value at minimum
y    = NLL_poisson( x, data ) - NLL_poisson( xmin, data )

# numerical derivative through difference quotient
dy  = np.gradient( y, dx )
ddy = np.gradient( dy, dx )

# graphical solution: find interval by identifying points where NLL - NLL(min) = 0.5 
# technique: using indexes in sorted arrays left and right of the minimum
ilo = np.searchsorted( -y[:imin], -0.5, side='left' )
ihi = imin + np.searchsorted( y[imin:], 0.5, side='right' )

# comparison with parabola using second derivative at minimum
plot = ax.plot( x, NLL_parabola(x, x[imin], 0, ddy[imin] ), '--', label="2nd derivative:\t\t" + r"$%4.2f \pm %4.2f$" % ( x[imin], 1./np.sqrt(ddy[imin]) ) )
ax.vlines( x[imin], 0, 1.25, plot[-1].get_color(), 'dotted' )

plot = ax.plot( x, y, label="graphical solution:\t" + r"$%4.2f^{+%4.2f}_{-%4.2f}$" % ( x[imin], x[ihi] - x[imin], x[imin] - x[ilo] ) )
ax.hlines( 0.5, 0, 10, plot[-1].get_color(), 'dotted' )
ax.vlines( [x[ilo], x[ihi]], 0, 1.25, plot[-1].get_color(), 'dotted' )

ax.set_xlabel( r'$\nu$' )
ax.set_ylabel( r'$\Delta(-\ln L(\nu))$' )
ax.set_xlim( xmin-2, xmin+2 )
ax.set_ylim(0,2)
ax.legend()

plt.show()


### Hypothesis testing
One of the most important questions about data is whether it supports (scientific, political, ...) hypotheses or whether hypotheses must be rejected on the basis of the data. In statistics, there are clearly defined **quantitative test procedures**, which are referred to as **hypothesis tests**. The basic task of a hypothesis test is to compare a sample of data with one or more hypotheses $H_i$ and to answer the questions:
- Can some of the hypotheses $H_i$ be **rejected** based on the data?
- If so, how sure are we that the rejection was **correct**?

In hypothesis tests with more than one hypothesis, one of the hypotheses often occupies a special position, the **null hypothesis** $H_0$. It often corresponds to the current state of knowledge and is compared with alternative hypotheses that take new effects into account.

>**Important**: Statistical test procedures only allow **rejection** of one or more hypotheses, a hypothesis can never be **proven**! There could always be better alternatives that have not been tested.

A hypothesis test consists of four steps:
1. Definition of a test statistic to distinguish between hypotheses.
2. Definition of criteria for rejecting the null hypothesis.
3. Measurement of the test statistic.
4. Decision.

These four steps are explained in more detail below.

An **example** of a hypothesis from the scientific literature is the question of smoking as a cause of lung cancer. The following data set is taken from the report *Occupational Mortality: The Registrar General's Decennial Supplement for England and Wales, 1970-1972, Her Majesty's Stationery Office, London, 1978*. It contains two indicator variables for 25 groups of people:
- Smoking index: assumes a value of 100 if number of cigarettes per day is the average for all men of the same age.
- Lung cancer index: assumes a value of 100 if the number of lung cancer deaths corresponds to the average.

Using these data, two hypotheses are tested in the following code example. Hypothesis $H_0$ states that there is no correlation between the two variables, hypothesis $H_1$ that the lung cancer index increases with the smoking index. Here we have (arbitrarily) chosen "no correlation" as the null hypothesis. The question now is whether $H_0$ can be rejected on the basis of the data. If we plot the two variables against each other in a scatter plot, $H_0$ corresponds to a horizontal straight line and $H_1$ to a straight line with a positive slope. In this case, the correlation coefficient could be used as a variable to differentiate between the hypotheses (test variable, see below) and the question could be asked as to whether one of the hypotheses must be rejected on the basis of the correlation coefficient.

In [ ]:
"""Hypothesis testing: smoking as a cause for lung cancer?"""

import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit

def H0_model( x, a0=1. ):
	return np.repeat( a0, len(x) ) # as x is ignored in this model, return a0 for every x value
	
def H1_model( x, a0=1., a1=1. ):
	'''Alternative hypothesis: straight line'''
	return a0 + a1*x

data = np.genfromtxt('data/smoking.csv', delimiter=",", skip_header=4 )
xdata, ydata = data[:,0], data[:,1]

fig,ax = plt.subplots()
ax.scatter( xdata, ydata, label="Data" )
ax.set_xlabel( "Smoking Index")
ax.set_ylabel( "Lung Cancer Index")
ax.text( 110, 52, "Correlation Coefficient: %5.3f" % np.corrcoef(data,rowvar=False)[0][1] )

xrange = np.linspace( 65, 145, 320 )

# Fit and plot H0 with scipy.optimize.curve_fit
popt, pcov = curve_fit( H0_model, xdata, ydata )
ax.plot( xrange, H0_model( xrange, *popt ), 'r', label="$H_0$" ) 

# Fit and plot H1 with scipy.optimize.curve_fit
popt, pcov = curve_fit( H1_model, xdata, ydata )
ax.plot( xrange, H1_model( xrange, *popt ), 'g', label="$H_1$" ) 

ax.legend()

plt.show()


#### Step 1 - Definition of the test statistic
In the code example above, the original sample ("raw data") has already been pre-processed: Individuals have been divided into groups of people and the smoking index and lung cancer index variables have been defined so that they are normalized to their average. The hypotheses differ on the basis of the gradient of the straight lines in the scatter diagram of these variables or in the expected correlation coefficient. Both are zero for $H_0$ and different from zero for $H_1$. In general, a function of the data $\mathbf{x}=(x_1, \dots, x_n)$ must be found for a hypothesis test, which can be used to **distinguish** between different hypotheses. This quantity is referred to as the **test statistic** $t(\mathbf{x})$:
- $t(\mathbf{x})$ can in principle be any scalar function of the data. An example of a test statistic is the likelihood function $L(H_i|\mathbf{x})$.
- $t(\mathbf{x})$ is a random variable that follows different PDFs $g(t|H_i)$ under different hypotheses. This is illustrated schematically in the following code example. The PDF chosen (arbitrarily, for illustrative purposes) is a piecewise defined function, a normal distribution with different scaling parameters to the left and right of the maximum.

In [ ]:
"""Illustration of hypothesis testing"""
import numpy as np
import matplotlib.pyplot as plt 
from scipy.stats import norm

def double_gaussian_model( x, mu=0., sigma1=1., sigma2=2. ):
	'''Normal distributions with different sigmas left and right of mu:'''
	fac=2./(sigma1+sigma2)
	return np.where( x < mu, fac*sigma1*norm.pdf( x, loc=mu, scale=sigma1), fac*sigma2*norm.pdf( x, loc=mu, scale=sigma2) )

# range of values
tmin, tmax = 0, 10
t = np.linspace( tmin, tmax, 200 )

fig,ax = plt.subplots()
ax.plot( t, double_gaussian_model( t, 3 ), label="$H_0$" )
ax.set_xlabel( "test statistic $t$" )
ax.set_ylabel( "$g(t|H_i)$")
ax.set_ylim( 0, 0.4 )
ax.legend()

plt.show()

>**Note: Types of hypotheses** 
>
>Since hypotheses in hypothesis tests are formulated as PDFs of the test statistic $g(t|H_i)$, they can be classified according to the parameter dependency of the test statistic. The PDFs describing the hypotheses can depend on two types of parameters: The parameters $\boldsymbol{\lambda}$ are already known before the hypothesis test, and the parameters $\boldsymbol{\theta}$ are unknown and must be determined from the data.
>- Hypotheses for which **all parameters of the PDF are known** are referred to as **simple hypotheses**: $g(t|H_i(\boldsymbol{\lambda}))$. Example: Data in a counting experiment follow a Poisson distribution with known parameter $\nu=5$.
>- For **composite hypotheses** the PDF is known except for some parameters $\boldsymbol{\theta}$: $g(t|H_i(\boldsymbol{\lambda},\boldsymbol{\theta}))$. Example: Data follow a normal distribution with known localization parameter $\mu$ but unknown scaling parameter $\sigma$, which must be determined from data.

>**Note: Choice of test statistic** 
>
>A clever choice of test statistic is important in order to obtain a hypothesis test that is as meaningful as possible. There is an auxiliary mathematical theorem, the **Neyman-Pearson lemma**, which states that if for two simple hypotheses $H_0$ and $H_1$ the likelihood functions $L(H_0)$ and $L(H_1)$ are completely known, the **likelihood ratio**
>$$
r(\mathbf{x}) =
\frac{L(H_0|\mathbf{x})}{L(H_1|\mathbf{x})} =
\frac{\prod_{i=1}^n f(x_i|H_0)}{\prod_{i=1}^n f(x_i|H_1)}
>$$
> is the **optimal test statistic**. The problem with using the Neyman-Pearson lemma in practice is that the likelihood functions are often unknown. Therefore, the following approaches are often chosen instead:
>- Plausible **ansatz** for functional form of the test variable.
>- Approximation of the likelihood functions, for example through **simulation** with the Monte-Carlo method
>- **Asympotic** approximation in the limiting case of large samples (keyword: [Wilks' theorem](https://en.wikipedia.org/wiki/Wilks%27_theorem), also works for composite hypotheses)
>
>The derivation of statistical quantities from data whose likelihood is unknown is an active field of research that is often referred to as **likelihood-free inference** or **simulation-based inference**.

#### Step 2 - Definition of criteria for rejecting the null hypothesis

The measurement in the following step 3 provides a measured value $t=t_1$ for the test statistic. Before the measurement, the minimum value $t_0$ that the measured value must assume in order to reject the null hypothesis must be determined. The test statistic is selected (according to the usual convention) in such a way that larger values of $t$ imply poorer agreement with the null hypothesis. The illustration above shows that many PDFs $g(t|H_i)$ have non-zero values for all $t\in\mathbb{R}$. For each $t_0<\infty$, there is therefore a finite probability that the **null hypothesis will be rejected even though it is true**. This situation is discussed below as an "type-I error" and must practically always be accepted in hypothesis tests - a **hypothesis can never be rejected with one hundred percent certainty**. The maximum permissible probability of error $\alpha$ is referred to as the **significance level** and must always be **determined before the measurement**. Mathematically, this is formulated as follows
$$
\int_{t_0}^\infty g(t|H_0)\mathsf{d}t = \alpha.
$$
A value $t_0$ must therefore be chosen so that the probability that $t_1\geq t_0$ is measured, even if the null hypothesis is true, is equal to $\alpha$. The code example below shows the geometric interpretation of the equation: A value $t_0$ is sought for which the area under the curve to the left of $t_0$ assumes the value $\alpha$.

#### Step 3 - Measurement of the test variable
Only **after** determining the significance level is the test variable measured; this results in a value $t=t_1$. For this value, we also calculate the probability that $t\geq t_1$ is measured if the null hypothesis is true. This value is referred to as the **p value**:
$$
p = P(t\geq t_1|H_0)=\int_{t_1}^\infty g(t|H_0)\mathsf{d}t.
$$

>**Excursus: What is a p-value (and what is it not)?**
>
>Although significance level and p-value are defined by the same integral, they must be distinguished carefully:
>- The significance level $\alpha$ is the probability of a type-I error, i.e., the probability that the null hypothesis is rejected even though it is true, which always has to be accepted in hypothesis testing. The significance level is **determined before the measurement**.
>- The p-value is the probability that a value of $t\geq t_1$ is measured if the null hypothesis is true. It can only be determined **after $t_1$ has been measured**.
>
>Misunderstandings or inaccuracies are often found in connection with the p-value. It is therefore worth listing what a p-value **is not**, among other things:
>- The p-value is **not** the probability that the null hypothesis is true.
>- The p-value is **not** the probability of falsely rejecting the null hypothesis.
>- The p-value is **not** the probability that the measurement is "just a fluctuation".
>
> **The p-value is the probability that a value of $t\geq t_1$ is measured if the null hypothesis is true** - no more and no less!

In [ ]:
"""Illustration of hypothesis testing"""
import numpy as np
import matplotlib.pyplot as plt 
from scipy.stats import norm

def double_gaussian_model( x, mu=0., sigma1=1., sigma2=2. ):
	'''Normal distributions with different sigmas left and right of mu:'''
	fac=2./(sigma1+sigma2)
	return np.where( x < mu, fac*sigma1*norm.pdf( x, loc=mu, scale=sigma1), fac*sigma2*norm.pdf( x, loc=mu, scale=sigma2) )

# range of values
tmin, tmax, t0, t1 = 0, 10, 7, 5.2
t = np.linspace( tmin, tmax, 500 )
g = double_gaussian_model( t, 3, 1, 2 )

fig,ax = plt.subplots()

# plot PDF
ax.plot( t, g, label="$H_0$" )
ax.set_xlabel( "test statistic $t$" )
ax.set_ylabel( "$g(t|H_i)$")
ax.set_ylim( 0, 0.4 )
ax.legend()

# plot significance level
ax.vlines( t0, 0, 0.2, colors="green" )
ax.text( t0, -0.02, "$t_0$", color="green", ha="center" )
ax.fill_between( t[t>t0], 0, g[t>t0], facecolor="green", alpha=0.3 )
ax.annotate( r"$\alpha$", xy=(t0+0.25,0.02), xytext=(t0+1,0.07), arrowprops=dict(facecolor="black", width=1, headwidth=5) )

# plot measurement
ax.vlines( t1, 0, 0.2, colors="red" )
ax.text( t1, -0.02, "$t_1$", color="red", ha="center" )

plt.show()

#### Step 4: Decision
The decision is now made based on a comparison of the p-value for the measured value $t_1$ of the test variable with the significance level defined before the measurement:
- The hypothesis $H_0$ is **rejected** if the **p-value is below the significance level**: $p<\alpha$. This corresponds to $t_1>t_0$. The hypothesis then still has a probability of being true.
- If the **p-value is above the significance level**, i.e. $p\geq\alpha$ or $t_1\leq t_0$, then the hypothesis $H_0$ **cannot be rejected**, although it may be false.

#### Comparison of hypotheses
The next step in testing hypotheses is to compare an alternative hypothesis $H_1$ with the null hypothesis $H_0$. This raises the question of how well the hypotheses can be differentiated at a given significance level $\alpha$. The code example below shows the PDF of the null hypothesis $g(t|H_0)$ as well as that of the alternative hypothesis $g(t|H_1)$. The red area shown there
$$
\beta = \int_{-\infty}^{t_0} g(t|H_1)\mathsf{d}t
$$
corresponds to the probability of not rejecting the null hypothesis, even if the alternative hypothesis is true. This is referred to as the "type-II error" and is discussed briefly below.

In [ ]:
"""Illustration of hypothesis testing"""
import numpy as np
import matplotlib.pyplot as plt 
from scipy.stats import norm
from scipy.integrate import quad

def double_gaussian_model( x, mu=0., sigma1=1., sigma2=2. ):
	'''Normal distributions with different sigmas left and right of mu'''
	fac=2./(sigma1+sigma2)
	return np.where( x < mu, fac*sigma1*norm.pdf( x, loc=mu, scale=sigma1), fac*sigma2*norm.pdf( x, loc=mu, scale=sigma2) )

# range of values
tmin, tmax, t0, t1 = 0, 10, 7, 5.2
t = np.linspace( tmin, tmax, 500 )
g0 = double_gaussian_model( t, 3, 1, 2 )
g1 = double_gaussian_model( t, 8.5, 1.5, 1)

fig,ax = plt.subplots()

# plot PDFs
ax.plot( t, g0, label="$H_0$" )
ax.plot( t, g1, label="$H_1$" )
ax.set_xlabel( "Test Statistic $t$" )
ax.set_ylabel( "$g(t|H_i)$")
ax.set_ylim( 0, 0.4 )
ax.legend()

# plot significance level alpha
ax.vlines( t0, 0, 0.3, colors="green" )
ax.text( t0, -0.025, "$t_0$", color="green", ha="center" )
ax.fill_between( t[t>t0], 0, g0[t>t0], facecolor="green", alpha=0.3 )
ax.annotate( r"$\alpha$", xy=(t0+0.25,0.02), xytext=(t0+1,0.07), arrowprops=dict(facecolor="black", width=1, headwidth=5) )

# plot test power beta
ax.fill_between( t[t<t0], 0, g1[t<t0], facecolor="red", alpha=0.3 )
ax.annotate( r"$\beta$", xy=(t0-1.5,0.02), xytext=(t0-2.5,0.07), arrowprops=dict(facecolor="black", width=1, headwidth=5) )

plt.show()

The value $1-\beta$ is referred to as the (discriminatory) **power** of the test. It indicates the probability of $t>t_0$ if the alternative hypothesis $H_1$ is true. As the significance level $\alpha$ is fixed at $t_0$, $1-\beta$ is a measure of how well the hypotheses differ. The less overlap the two PDFs have, the greater the power of the test. A good test statistic should minimize this overlap as much as possible.

>**Excursus: Error types**
>
>The types of error mentioned in this section will be summarized again here. It is important to note that hypothesis tests (like all scientific statements) **never provide absolutely true results** - errors must always be accepted!
>
>A **type-I error** (also called **false positive**) is committed when the **null hypothesis is rejected, even if it is true**. In hypothesis tests, the probability $\alpha$ for type-I errors is determined **before** the measurement. Examples of type-I errors are:
>- A disease is falsely diagnosed in healthy patients.
>- A new elementary particle is discovered by mistake. The usual significance level for this in physics is $\alpha=3\times 10^{-7}$.
>- Honest customers are classified as fraudsters.
>
>A **type-II error** (also called **false negative**) is committed when the **null hypothesis is not rejected even if it is false**. In hypothesis tests with an alternative hypothesis, the probability $\beta$ for type-II errors is implicitly determined by $\alpha$ before the measurement. Examples of type-II errors include:
>- A disease is not diagnosed in sick patients.
>- A new elementary particle is not detected even though it is present in the data. A significance level of $\alpha=5\%$ or $\alpha=10\%$ is common for this.
>- A fraud is not detected.

### Statistical classification
While the null hypothesis often assumes a special role in hypothesis tests, statistical classification is concerned with the **comparison of several equivalent hypotheses**. The aim is to divide data into two or more classes according to their features. To do this, a classifier must be found that offers the best possible discriminatory power between the classes. The features themselves and any function of the features are generally suitable as classifiers. For example, data could be searched for a distinction between signal and background. This divides the data into two classes, also known as **binary classification**. In image recognition, several classes are often required, e.g. to differentiate between dogs, cats, mice, cars, etc. This type of classification is called **multiclass classification**.

The following code shows a binary classification between signal (red) and background (blue) based on two features. In this case, a linear classifier can be guessed "by eye": a diagonal straight line separates the two classes; it corresponds to a linear combination of the two features.

In [ ]:
"""Example of binary classifications: two fuzzy rings"""

import numpy as np
import matplotlib.pyplot as plt 

rng = np.random.default_rng( 42 )

def random_ring( center=[0,0], radius=1, width=0.2, N=100 ):
    """generate random numbers: radius from normal distribution, uniform polar angle,
    return array of x and y from coordinate transformation, shifted by center"""
    r   = rng.normal( loc=radius, scale=width, size=N )
    phi = rng.uniform( 0, 2*np.pi, size=N )
    return [ center[0]+r*np.cos(phi), center[1]+r*np.sin(phi) ]

# create synthetic data: two intersecting rings
N = 200
ring1 = random_ring( [1,1], 2, 0.2, N )
ring2 = random_ring( [-1,-1], 2, 0.5, N )

fig,ax = plt.subplots()
ax.scatter( ring1[0], ring1[1], color="r", label="Signal" )
ax.scatter( ring2[0], ring2[1], color="b", label="Background" )

# create by-eye discriminant
xl = np.linspace( -3, 3, 300 )
ax.plot( xl, -xl, color="green", linewidth=2, label="Classifier" )
ax.set_xlabel("Feature 1")
ax.set_ylabel("Feature 2")
ax.legend()

plt.show()


>**Note: Linear classification** 
>
>Instead of performing the above classification "by eye", there is a mathematical method to find a linear classifier, which was developed by Ronald Aylmer Fisher in 1936, and which leads to the **Fisher discriminant**, which is described in many textbooks of statistical data analysis, see e.g. [Wikipedia article on linear discriminant analysis](https://en.wikipedia.org/wiki/Linear_discriminant_analysis).


### Machine learning
Linear discriminant analysis has its limitations: it can be shown that it only works optimally for linear classification problems. There are a number of non-linear classification methods, many of which now rely on machine learning (ML). Machine learning involves a learning process that is often referred to as **training**. The classifier has trainable parameters that are optimized within the learning process. For this purpose, the classifier is provided with data with known true classification (labeled data) as input variables. A distinction is made between the following types of machine learning:
- Currently, **supervised learning** is the most important variant of machine learning. Here, the output of the classifier is compared with the known classification of the training data and the trainable parameters are optimized so that the difference between the output of the classifier and the true classification is minimized.
- In **unsupervised learning**, the classifier is trained based solely on the patterns of the input variables.
- In **reinforcement learning**, a correct classification is "rewarded".

A good online resource for getting started with machine learning is the e-book [Deep Learning](http://deeplearningbook.org) by Ian Goodfellow, Yoshua Bengio and Aaron Courville.

>**MNIST dataset**
>
> In the research field of machine learning, there are several standard datasets that are used to compare classification methods. One of these is a modified version of a database of handwritten digits from the National Institute of Standards and Technology NIST (Modified NIST, MNIST), the US equivalent of the German Physikalisch-Technische Bundesanstalt PTB. In the days of hand-addressed letters, the automatic recognition of these digits was used, for example, to automatically read out zip codes. The data set for training an AI consists of 60,000 images, in addition there are 10,000 more images for an independent test of the AI; each image is a matrix of $28\times 28$ pixels with 255 gray levels with **known** classification. The task is a multi-class classification with ten classes, the digits from 0 to 9. A random selection of these images is shown below.
>
><img src="img/mnist.png" width=60%>

#### Neural networks
A large number of non-linear classifiers can be found in the literature, and different scientific fields favor different classifiers. In particle physics, for example, **boosted decision trees** (BDTs) and artificial **neural networks** (NNs) have been the most common classifiers since the early 2000s. Due to the ongoing trend of deep learning, variants of deep neural networks play by far the most important role in the field of machine learning today, from image recognition with convolutional neural networks (CNNs) to large language models (LLMs) such as in ChatGPT.

Neural networks are modeled on the human brain. Schematically, a neuron consists of dendrites, which supply it with input data, the synapse, which combines and weighs this data, and the axon, which compares the weighted sum of the signals with a threshold and decides whether an output signal is generated. The output of a neuron is therefore a non-linear function of the input data, which can be passed on to other neurons. This is illustrated in the following figure:

<img src="img/neuron_brain.png" width=50%>

A simple example of an artificial neural network is the **feed-forward NN**. This NN consists of several layers of neurons (also called "nodes" in this context). The layers include:
- **Input layer**, with $n$ nodes, which can thus process $n$ features,
- One or more **hidden layers**, usually with more than $n$ nodes,
- **Output layer**, with one node (binary classification) or more nodes (multiclass classification).

Each neuron in a layer is usually connected to all neurons in the subsequent layer (fully-connected layers, dense layers), as shown in the following figure:

<img src="img/multi_layer_perceptron.png" width=80%>

In feed-forward NNs, data is always "forwarded" from layer to layer (left to right in the above figure), hence the name. The training optimizes the strength of all connections between neurons, expressed by weights. The quantity $w_{ij}^{(k)}$ is the weight between neuron $i$ of the $k-1$th layer and neuron $j$ of the $k$th layer.
For the purpose of training, the output of the NN is compared with the true classification using a suitable **loss function** and the weights are optimized so that the loss function is minimized. Modern numerical optimization algorithms are used for this.

#### Example: MNIST dataset with Keras
The currently leading software packages for machine learning in Python are [`TensorFlow`](https://www.tensorflow.org) and [`PyTorch`](https://pytorch.org). The following example uses TensorFlow via the frontend [`Keras`](https://keras.io), which greatly simplifies access to the TensorFlow functionality. To run the example below, TensorFlow and Keras must be installed on the computer or server running the Jupyter notebook. On the [Jupyter server of the SCC](https://jupyter-test.scc.kit.edu) this currently works with the server `GPU Jupyter`. On your own computer you can install the packages with `pip install tensorflow` or in Anaconda with `conda create -n tf tensorflow; conda activate tf`.

The following code example first defines the hyperparameters of the model, then loads the MNIST images and displays a selection graphically. Then the model is defined: it is a fully connected feed-forward NN with one hidden layer.
The minimization algorithm is Adam (see section on numerical optimization) and the loss function is the [categorical cross entropy](https://en.wikipedia.org/wiki/Cross-entropy). Finally, the model is trained and the accuracy of the classification, i.e., the fraction of correctly classified images, is output. Feel free to try out other NN architectures and hyperparameters.

In [ ]:
"""Statistical classification: NN from Keras/TensorFlow classifying MNIST dataset"""
from tensorflow.keras.datasets import mnist
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.utils import plot_model, to_categorical
import numpy as np
import matplotlib.pyplot as plt

# hyperparameters of Keras model
batchsize = 100
nclasses  = 10
epochs    = 20
dropout   = 0.2

In [ ]:
# MNIST dataset: 60000 (train) + 10000 (test) images (28x28 pixels, 8 bit grayscale)
datasize  = 28*28
( x_tr, y_tr ), ( x_te, y_te ) = mnist.load_data()

# show a matrix of random images
N = 15
rng = np.random.default_rng( 42 )
pics=rng.integers( 0, len(x_tr), N*N )

fig,ax = plt.subplots(N,N)
for a, i in zip( ax.reshape(-1), pics ):
    a.set_axis_off()
    a.imshow( x_tr[i] )
plt.savefig( "mnist.pdf" )

# NNs require feature *vectors* as inputs, therefore re-format the images (28x28) as vectors with 784 entries
x_tr = x_tr.reshape( 60000, datasize )

# scale the 255 shades of gray (8-bit integer) to float between 0 and 1
x_tr = x_tr.astype( 'float32' )
x_tr /= 255

# translate 10 categories (numbers 0..9) as matrix for Keras
y_tr = to_categorical( y_tr, nclasses )

# same processing for test data
x_te = x_te.reshape( 10000, datasize )
x_te = x_te.astype( 'float32' )
x_te /= 255
y_te = to_categorical( y_te, nclasses )

In [ ]:
# construct the model: feed-forward network with 1-3 hidden layers
model = Sequential()
model.add( Dense( 100, activation = 'relu', input_shape = ( datasize, ) ) )
#model.add( Dense( 100, activation = 'relu' ) )
#model.add( Dense( 100, activation = 'relu' ) )
model.add( Dense( nclasses, activation = 'softmax' ) )
model.summary()

# build model with ADAM optimizer and categorical cross-entropy as loss function
model.compile( optimizer = 'adam',
                loss = 'categorical_crossentropy',
                metrics = [ 'accuracy' ] )

In [ ]:
# train the model
history = model.fit( x_tr, y_tr,
                    epochs = epochs,
                    batch_size = batchsize,
                    verbose = 1,
                    validation_data = ( x_te, y_te ) )

# evaluate the previously trained model on test dataset
score = model.evaluate( x_te, y_te, verbose = 0 )
print( "loss function value after training:", score[0] )
print( "fraction of correctly classified images (accuracy):", score[1] )

# Closing remarks
The course **Computer-guided Data Analysis** (CgDA) was your first introduction to working with data on the computer in physics studies. It is an important **key qualification** for your studies, especially with regard to physics laboratory courses and Bachelor and Master theses. It also contributes significantly to the key qualification of **data literacy**. Much of the computer application in physics is **"learning by doing"** - as with any tool, the best way to learn how to use it is by using it regularly. The lecture materials (slides and lecture notes with examples, exercises) provide you with a good basis for the rest of your studies.

**Keep the ball rolling - curious and creative minds are needed!**
